# Simplifying the coating thermal noise calculation of Hong et al

Following [Yam et al](https://doi.org/10.1103/PhysRevD.91.042002), specialize the calculation of [Hong et al](https://doi.org/10.1103/PhysRevD.87.082001) to the case of no photoelastic effects and no bulk/shear asymmetry.

In [1]:
import sympy as sp

Define symbols from Hong et al; use $\phi^l_j$ for the coating bulk and shear loss angle (not to be confused with phase $\phi_j$).

In [2]:
f, k_b, T, l_j, λ_j, Y_s, Y_j, σ_s, σ_j, φl_j, A_eff, a_j = sp.symbols("f k_b T l_j λ_j Y_s Y_j σ_s σ_j φ^l_j A_eff a_j")

The following transfer functions are defined in table 1.

In [3]:
CB_j = sp.sqrt((1+σ_j)/2)

In [4]:
DB_j = (1-σ_s-2*σ_s**2)/sp.sqrt(2*(1+σ_j)) * Y_j/Y_s

In [5]:
CSA_j = sp.sqrt(1-2*σ_j)

In [6]:
DSA_j = -(1-σ_s-2*σ_s**2)/(2*sp.sqrt(1-2*σ_j)) * Y_j/Y_s

In [7]:
DSB_j = (sp.sqrt(3)*(1-σ_j)*(1-σ_s-2*σ_s**2))/(2*sp.sqrt(1-2*σ_j)*(1+σ_j)) * Y_j/Y_s

Bulk and shear losses are assumed identical, so $S_j^B = S_j^S = S_j$ (see eq 96).

In [8]:
S_j = 4*k_b*T*λ_j*φl_j*(1-σ_j-2*σ_j**2)/(3*sp.pi*f*Y_j*(1-σ_j)**2*A_eff)

The thermal phase noise (in displacement units) is given in eq 94. Ignoring photoelastic effects ($\beta_j \rightarrow 0$), none of the quantities inside the integral has a $z$ dependence, so the integral reduces to $l_j$. For brevity, define $a_j = 1 - \mathrm{Im}\frac{\epsilon_j}{2}$ (where $\epsilon_j = n_j \frac{\partial \log \rho}{\partial \phi_j}$ in the absence of photoelastic effects).

In [9]:
S_ξ = l_j/λ_j * S_j * ((a_j*CB_j + DB_j)**2 + (a_j*CSA_j + DSA_j)**2 + DSB_j**2)

Divide out the pre-factors in Yam et al eq 1 to find $b_j$. (Also divide out $1/(1-\sigma_j)$ which is the pre-factor inside $b_j$.)

In [10]:
b_j = S_ξ / (2*k_b*T/(sp.pi*f*A_eff) * (1-σ_s-2*σ_s**2)/Y_s * l_j * φl_j * 1/(1-σ_j))

Represent $b_j (1-\sigma_j)$ as a polynomial in $a_j$ and simplify its coefficients, thus extracting the two terms as written in Yam et al.

In [11]:
coeffs_b_j = reversed(sp.Poly(b_j, a_j).coeffs())
sum([a_j**n * sp.simplify(coeff) for (n, coeff) in enumerate(coeffs_b_j)])

-Y_j*(2*σ_s**2 + σ_s - 1)/(Y_s*(σ_j + 1)) + Y_s*a_j**2*(2*σ_j**2 + σ_j - 1)/(Y_j*(2*σ_s**2 + σ_s - 1))

This does not match the expression found in Yam et al, but it agrees with the other CTN computations tested by Gabriele's [thermal noise models](https://git.ligo.org/gabriele-vajente/thermal-noise-models) code.